# Assembler rubustness - Table Metrics

In [17]:
import sys
from plotly.offline import plot
import glob
import fnmatch
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import json
import pandas as pd
from itertools import groupby
import csv
import numpy as np

In [18]:
METRICS_COLUMNS_GLOBAL = ['run','sample','assembler', 'contigs', 'basepairs', 'max_contig', 'Ns', 'n50', 'misassemblies', 'mapped_reads']
ASSEMBLER_PROCESS_LIST = ["BCALM2", "GATBMINIAPIPELINE", "MINIA", "MEGAHIT", "METASPADES", "UNICYCLER", "SPADES",
                          "SKESA", "VELVETOPTIMIZER", "IDBA"]
PROCESS_TO_NAME = {"BCALM2": "BCALM2", 
                   "GATBMINIAPIPELINE": "GATBMiniaPipeline",
                   "MINIA": "MINIA",
                   "MEGAHIT": "MEGAHIT", 
                   "METASPADES": "metaSPAdes", 
                   "UNICYCLER": "Unicycler", 
                   "SPADES": "SPAdes",
                    "SKESA": "SKESA",
                   "VELVETOPTIMIZER": "VelvetOptimizer",
                   "IDBA": "IDBA-UD"}
log_distributed = ['LHS', 'LNN', 'ERR2935805']
even_distribution = ['EHS', 'LNN', 'ERR2984773']
METRICS_COLUMNS_REFERENCE = ['run','sample','assembler', 'reference', 'contiguity', 'breadth_of_coverage', 'multiplicity', 'validity', 
                             'parsimony', 'identity', 'lowest_identity', 'L90', 'contigs', 'NA50', 'NG50', 'basepairs', 'Ns',
                             'misassemblies']

## Global Metrics

In [19]:
report_glob = glob.glob('../Results/*/report/pipeline_report_tables.json')
global_pipeline_metrics_df = pd.DataFrame(columns=METRICS_COLUMNS_GLOBAL)

for pipeline_report_file in report_glob:
    report_file_name = pipeline_report_file.split('/')[-1]
    stats_run = pipeline_report_file.split('/')[-3]
    print('Processing {0} data from {1}...'.format(report_file_name, stats_run))
    
    with open(pipeline_report_file) as _fh:
        json_report = json.load(_fh)
        for sample in json_report.keys():
            for line in json_report[sample]['GlobalTable']:
                assembler = line['assembler']
                global_pipeline_metrics_df = global_pipeline_metrics_df.append({'run': stats_run,
                                                                                'sample': sample,
                                                                                'assembler': line['assembler'],
                                                                                'contigs': line['original']['contigs'],
                                                                                'basepairs': line['original']['basepairs'],
                                                                                'max_contig': line['original']['max_contig_size'],
                                                                                'n50': line['original']['N50'],
                                                                                'mapped_reads': line['original']['mapped_reads'],
                                                                                'Ns': line['original']['Ns'],
                                                                                'misassemblies': line['filtered']['misassembled_contigs']},
                                                                               ignore_index=True)
global_pipeline_metrics_df['distribution'] = np.where(global_pipeline_metrics_df['sample'].isin(log_distributed), 'Log', 'Even')
display(global_pipeline_metrics_df)

Processing pipeline_report_tables.json data from run3...
Processing pipeline_report_tables.json data from run2...
Processing pipeline_report_tables.json data from run1...


run sample          assembler contigs basepairs max_contig     Ns  \
0    run3    ENN             BCALM2   25293  31046921     161812      0   
1    run3    ENN  GATBMiniaPipeline    1047  30453713     632215      0   
2    run3    ENN            IDBA-UD    1845  30395584     493975      0   
3    run3    ENN            MEGAHIT     809  30544991     632274      0   
4    run3    ENN         metaSPAdes     636  30459024    1036942      0   
..    ...    ...                ...     ...       ...        ...    ...   
175  run1    EHS              MINIA   17453  30676667     161812      0   
176  run1    EHS              SKESA    2009  30081658     474592      0   
177  run1    EHS             SPAdes    7786  30958558     847495      0   
178  run1    EHS          Unicycler     705  30388464     882570      0   
179  run1    EHS    VelvetOptimizer   15622  31184863     846904  25898   

        n50 misassemblies  mapped_reads distribution  
0     17766             0     91.373194         Even  
1     95947             1     99.564049         Even  
2     63282            15     98.579361         Even  
3    173579             6     99.786631         Even  
4    245937             1     99.342639         Even  
..      ...           ...           ...          ...  
175   18179             0     79.520276         Even  
176   44029             8     91.595230         Even  
177  196423             2     86.864229         Even  
178  242222             1     91.164218         Even  
179   27836            25     71.201116         Even  

[180 rows x 11 columns]

In [20]:
dfglobal = pd.DataFrame(columns=['Sample', 'Assembler', 'Contigs', "Basepairs", "Max Contig Size", "N", 'N50', 'Misassemblies', "Mapped Reads"])

for sample in sorted(global_pipeline_metrics_df['sample'].unique(), key=lambda v: v.upper(), reverse=True):
    for assembler in sorted(global_pipeline_metrics_df['assembler'].unique(), key=lambda v: v.upper(), reverse=True):
        
        #contigs
        contigs = global_pipeline_metrics_df['contigs'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler)]
        #diff_contigs = np.diff(contigs)
        #diff_contigs = (round(min(diff_contigs),2), round(max(diff_contigs),2))
        #if len(set(diff_contigs)) == 1:
        #    diff_contigs = diff_contigs[0]
        diff_contigs = round(max(contigs) - min(contigs),2)

        
        #basepairs
        basepairs = global_pipeline_metrics_df['basepairs'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler)]
        diff_basepairs = round(max(basepairs) - min(basepairs),2)
            
        #max contig size
        max_contig = global_pipeline_metrics_df['max_contig'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler)]
        diff_max_contig = round(max(max_contig) - min(max_contig),2)
        
        #Ns
        N = global_pipeline_metrics_df['Ns'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler)]
        diff_N = round(max(N) - min(N),2)
        
        #n50
        n50 = global_pipeline_metrics_df['n50'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler)]
        diff_n50 = round(max(n50) - min(n50),2)
        
        #misassembly
        misassembly = global_pipeline_metrics_df['misassemblies'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler)]
        diff_misassembly = round(max(misassembly) - min(misassembly),2)
        
        #mapped_reads
        mapped_reads = global_pipeline_metrics_df['mapped_reads'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler)]
        diff_mapped_reads = round(max(mapped_reads) - min(mapped_reads),2)
        
        #combine
        dfglobal = dfglobal.append({ 'Assembler': assembler, 'Sample': sample, 'Contigs': diff_contigs, "Basepairs": diff_basepairs, 
                        "Max Contig Size": diff_max_contig, "N": diff_N, 'N50': diff_n50, 'Misassemblies': diff_misassembly, 
                        "Mapped Reads": diff_mapped_reads}, ignore_index=True)

dfglobal

Sample          Assembler  Contigs  Basepairs Max Contig Size    N  \
0          LNN    VelvetOptimizer        0          0               0    0   
1          LNN          Unicycler        0          0               0    0   
2          LNN             SPAdes        0          0               0    0   
3          LNN              SKESA        0          0               0    0   
4          LNN              MINIA       17       1018               0    0   
5          LNN         metaSPAdes        0          0               0    0   
6          LNN            MEGAHIT        0          0               0    0   
7          LNN            IDBA-UD        2        410               0    0   
8          LNN  GATBMiniaPipeline        0          0               0    0   
9          LNN             BCALM2        0          0               0    0   
10         LHS    VelvetOptimizer        0          0               0    0   
11         LHS          Unicycler        0          0               0    0   
12         LHS             SPAdes        0          0               0    0   
13         LHS              SKESA        0          0               0    0   
14         LHS              MINIA       28       1378               0    0   
15         LHS         metaSPAdes        0          0               0    0   
16         LHS            MEGAHIT        0          0               0    0   
17         LHS            IDBA-UD        0          0               0    0   
18         LHS  GATBMiniaPipeline        0          0               0    0   
19         LHS             BCALM2  2799577  141491907            4089    0   
20  ERR2984773    VelvetOptimizer   273368    9068813            3003  470   
21  ERR2984773          Unicycler        0          0               0    0   
22  ERR2984773             SPAdes        0          0               0    0   
23  ERR2984773              SKESA        0          0               0    0   
24  ERR2984773              MINIA       24       2718               0    0   
25  ERR2984773         metaSPAdes        0          0               0    0   
26  ERR2984773            MEGAHIT        0          0               0    0   
27  ERR2984773            IDBA-UD        8       1420               0    0   
28  ERR2984773  GATBMiniaPipeline        2       1022               0    0   
29  ERR2984773             BCALM2        0          0               0    0   
30  ERR2935805    VelvetOptimizer        0          0               0    0   
31  ERR2935805          Unicycler        0          0               0    0   
32  ERR2935805             SPAdes        0          0               0    0   
33  ERR2935805              SKESA        0          0               0    0   
34  ERR2935805              MINIA        4        640               0    0   
35  ERR2935805         metaSPAdes        0          0               0    0   
36  ERR2935805            MEGAHIT        0          0               0    0   
37  ERR2935805            IDBA-UD        3        648               0    0   
38  ERR2935805  GATBMiniaPipeline        4        112               0    0   
39  ERR2935805             BCALM2        0          0               0    0   
40         ENN    VelvetOptimizer        0          0               0    0   
41         ENN          Unicycler        0          0               0    0   
42         ENN             SPAdes        0          0               0    0   
43         ENN              SKESA        0          0               0    0   
44         ENN              MINIA        2        180               0    0   
45         ENN         metaSPAdes        0          0               0    0   
46         ENN            MEGAHIT        0          0               0    0   
47         ENN            IDBA-UD        0          0               0    0   
48         ENN  GATBMiniaPipeline        0          0               0    0   
49         ENN             BCALM2        0          0               0    0   
50         EHS    VelvetOptimi

In [26]:
for sample in sorted(dfglobal['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    df_per_sample = dfglobal[dfglobal['Sample']==sample]
    df_per_sample.to_csv('Tables/{} Global metrics.csv'.format(sample), index=False)

## Reference Metrics

In [27]:
global_pipeline_metrics_df = pd.DataFrame(columns=METRICS_COLUMNS_REFERENCE)

for pipeline_report_file in report_glob:
    report_file_name = pipeline_report_file.split('/')[-1]
    stats_run = pipeline_report_file.split('/')[-3]
    print('Processing {0} data from {1}...'.format(report_file_name, stats_run))
    
    with open(pipeline_report_file) as _fh:
        json_report = json.load(_fh)
        for sample in json_report.keys():
            for reference, data in json_report[sample]['ReferenceTables'].items():
                for row in data:
                    for item in row:
                        global_pipeline_metrics_df = global_pipeline_metrics_df.append({'run': stats_run,
                                                                                        'sample': sample,
                                                                                        'assembler': item['assembler'],
                                                                                        'reference': reference,
                                                                                        'contiguity': item['contiguity'],
                                                                                        'breadth_of_coverage': item['breadth_of_coverage'],
                                                                                        'multiplicity': item['multiplicity'],
                                                                                        'validity': item['validity'],
                                                                                        'parsimony': item['parsimony'],
                                                                                        'identity': item['identity'],
                                                                                        'lowest_identity': item['lowest_identity'],
                                                                                        'L90': item['L90'],
                                                                                        'contigs': item['aligned_contigs'],
                                                                                        'NA50': item['NA50'],
                                                                                        'NG50': item['NG50'],
                                                                                        'basepairs': item['aligned_basepairs'],
                                                                                        'Ns': item['Ns'],
                                                                                        'misassemblies': item['misassembled_contigs']},
                                                                                       ignore_index=True)

display(global_pipeline_metrics_df)

Processing pipeline_report_tables.json data from run3...
Processing pipeline_report_tables.json data from run2...
Processing pipeline_report_tables.json data from run1...


run sample          assembler                       reference  \
0     run3    ENN             BCALM2               Bacillus_subtilis   
1     run3    ENN  GATBMiniaPipeline               Bacillus_subtilis   
2     run3    ENN            IDBA-UD               Bacillus_subtilis   
3     run3    ENN            MEGAHIT               Bacillus_subtilis   
4     run3    ENN         metaSPAdes               Bacillus_subtilis   
...    ...    ...                ...                             ...   
2155  run1    EHS              MINIA  Staphylococcus_aureus_plasmid3   
2156  run1    EHS              SKESA  Staphylococcus_aureus_plasmid3   
2157  run1    EHS             SPAdes  Staphylococcus_aureus_plasmid3   
2158  run1    EHS          Unicycler  Staphylococcus_aureus_plasmid3   
2159  run1    EHS    VelvetOptimizer  Staphylococcus_aureus_plasmid3   

      contiguity  breadth_of_coverage  multiplicity  validity  parsimony  \
0       0.033684             0.976840      1.000279  1.000000   1.000279   
1       0.097833             0.983726      1.000000  0.999998   1.000002   
2       0.073639             0.982989      1.000898  1.000813   1.000085   
3       0.136495             0.986336      1.000156  1.001263   0.998894   
4       0.255293             0.985554      1.000000  1.000670   0.999330   
...          ...                  ...           ...       ...        ...   
2155    0.000000             0.000000      0.000000  0.000000   0.000000   
2156    0.433010             0.433010      1.000000  1.000000   1.000000   
2157    0.000000             0.000000      0.000000  0.000000   0.000000   
2158    0.390578             0.390578      1.000000  1.000000   1.000000   
2159    0.000000             0.000000      0.000000  0.000000   0.000000   

      identity  lowest_identity L90 contigs    NA50    NG50 basepairs Ns  \
0     1.000000         1.000000  65     115   65138   64934   3951981  0   
1     0.999754         0.993117  14      28  269695  269695   3979838  0   
2     0.999039         0.952862  31      52  122683  122683   3976856  0   
3     0.999911         0.998200  10      26  294549  315167   3990397  0   
4     0.998299         0.970149   8      18  552896  552896   3987235  0   
...        ...              ...  ..     ...     ...     ...       ... ..   
2155  0.000000         0.000000   0       0       0       0         0  0   
2156  1.000000         1.000000   0       1    1296       0      1296  0   
2157  0.000000         0.000000   0       0       0       0         0  0   
2158  1.000000         1.000000   0       1    1169       0      1169  0   
2159  0.000000         0.000000   0       0       0       0         0  0   

     misassemblies  
0                0  
1                0  
2                0  
3                1  
4                0  
...            ...  
2155             0  
2156             0  
2157             0  
2158             0  
2159             0  

[2160 rows x 18 columns]

In [29]:
dfreference = pd.DataFrame(columns=['Sample', 'Assembler', 'Reference', "Contiguity", "Breadth of Coverage", "Multiplicity", 'Validity', 
                           'Parsimony', "Identity", "lowest Identity", "L90", "Contigs", "NA50", "NG50", "Basepairs",
                          "Ns", "Misassemblies"])

for sample in sorted(global_pipeline_metrics_df['sample'].unique(), key=lambda v: v.upper(), reverse=True):
    for assembler in sorted(global_pipeline_metrics_df['assembler'].unique(), key=lambda v: v.upper(), reverse=True):
        for reference in sorted(global_pipeline_metrics_df['reference'].unique(), key=lambda v: v.upper(), reverse=True):
        
            #contiguity
            contiguity = global_pipeline_metrics_df['contiguity'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            #diff_contiguity = np.diff(contiguity)
            #diff_contiguity = (round(min(diff_contiguity),2), round(max(diff_contiguity),2))
            #if len(set(diff_contiguity)) == 1:
                #diff_contiguity = diff_contiguity[0]
            diff_contiguity = round(max(contiguity) - min(contiguity),2)
            
            #boc
            boc = global_pipeline_metrics_df['breadth_of_coverage'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_boc = round(max(boc) - min(boc),2)
            
            #multiplicity
            multiplicity = global_pipeline_metrics_df['multiplicity'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_multiplicity = round(max(multiplicity) - min(multiplicity),2)
            
            #validity
            validity = global_pipeline_metrics_df['validity'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_validity = round(max(validity) - min(validity),2)
            
            #parsimony
            parsimony = global_pipeline_metrics_df['parsimony'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_parsimony = round(max(parsimony) - min(parsimony),2)
            
            #identity
            identity = global_pipeline_metrics_df['identity'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_identity = round(max(identity) - min(identity),2)
            
            #lowest_identity
            lowest_identity = global_pipeline_metrics_df['lowest_identity'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_lowest_identity = round(max(lowest_identity) - min(lowest_identity),2)
            
            #L90
            L90 = global_pipeline_metrics_df['L90'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_L90 = round(max(L90) - min(L90),2)
            
            #contigs
            contigs = global_pipeline_metrics_df['contigs'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_contigs = round(max(contigs) - min(contigs),2)
            
            #NA50
            NA50 = global_pipeline_metrics_df['NA50'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_NA50 = round(max(NA50) - min(NA50),2)
            
            #NG50
            NG50 = global_pipeline_metrics_df['NG50'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_NG50 = round(max(NG50) - min(NG50),2)
            
            #basepairs
            basepairs = global_pipeline_metrics_df['basepairs'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_basepairs = round(max(basepairs) - min(basepairs),2)
            
            #Ns
            Ns = global_pipeline_metrics_df['Ns'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_Ns = round(max(Ns) - min(Ns),2)
            
            #Misassemblies
            Misassemblies = global_pipeline_metrics_df['misassemblies'][(global_pipeline_metrics_df['sample'] == sample) & (global_pipeline_metrics_df['assembler']==assembler) & (global_pipeline_metrics_df['reference'] == reference)]
            diff_Misassemblies = round(max(Misassemblies) - min(Misassemblies),2)
        
            #combine,
            dfreference = dfreference.append({ 'Assembler': assembler, 'Sample': sample, 'Reference': reference, 'Contiguity': diff_contiguity, 
                            "Breadth of Coverage": diff_boc, "Multiplicity": diff_multiplicity, 'Validity': diff_validity,
                            'Parsimony': diff_parsimony, "Identity": diff_identity, "lowest Identity": diff_lowest_identity,
                            "L90": diff_L90, "Contigs": diff_contigs, "NA50": diff_NA50, "NG50": diff_NG50,  "Basepairs": diff_basepairs,
                            "Ns": diff_Ns, "Misassemblies": diff_Misassemblies}, ignore_index=True)

dfreference

Sample        Assembler                       Reference  Contiguity  \
0      LNN  VelvetOptimizer  Staphylococcus_aureus_plasmid3         0.0   
1      LNN  VelvetOptimizer  Staphylococcus_aureus_plasmid2         0.0   
2      LNN  VelvetOptimizer  Staphylococcus_aureus_plasmid1         0.0   
3      LNN  VelvetOptimizer           Staphylococcus_aureus         0.0   
4      LNN  VelvetOptimizer             Salmonella_enterica         0.0   
..     ...              ...                             ...         ...   
715    EHS           BCALM2         Lactobacillus_fermentum         0.0   
716    EHS           BCALM2        Escherichia_coli_plasmid         0.0   
717    EHS           BCALM2                Escherichia_coli         0.0   
718    EHS           BCALM2           Enterococcus_faecalis         0.0   
719    EHS           BCALM2               Bacillus_subtilis         0.0   

     Breadth of Coverage  Multiplicity  Validity  Parsimony  Identity  \
0                    0.0           0.0       0.0        0.0       0.0   
1                    0.0           0.0       0.0        0.0       0.0   
2                    0.0           0.0       0.0        0.0       0.0   
3                    0.0           0.0       0.0        0.0       0.0   
4                    0.0           0.0       0.0        0.0       0.0   
..                   ...           ...       ...        ...       ...   
715                  0.0           0.0       0.0        0.0       0.0   
716                  0.0           0.0       0.0        0.0       0.0   
717                  0.0           0.0       0.0        0.0       0.0   
718                  0.0           0.0       0.0        0.0       0.0   
719                  0.0           0.0       0.0        0.0       0.0   

     lowest Identity L90 Contigs NA50 NG50 Basepairs Ns Misassemblies  
0                0.0   0       0    0    0         0  0             0  
1                0.0   0       0    0    0         0  0             0  
2                0.0   0       0    0    0         0  0             0  
3                0.0   0       0    0    0         0  0             0  
4                0.0   0       0    0    0         0  0             0  
..               ...  ..     ...  ...  ...       ... ..           ...  
715              0.0   0       0    0    0         0  0             0  
716              0.0   0       0    0    0         0  0             0  
717              0.0   0       0    0    0         0  0             0  
718              0.0   0       0    0    0         0  0             0  
719              0.0   0       0    0    0         0  0             0  

[720 rows x 17 columns]

In [31]:
for sample in sorted(dfreference['Sample'].unique(), key=lambda v: v.upper(), reverse=True):
    for reference in sorted(dfreference['Reference'].unique(), key=lambda v: v.upper(), reverse=True):
        df_per_sample = dfreference[(dfreference['Sample']==sample) & (dfreference['Reference']==reference)]
        df_per_sample.to_csv('Tables/{} {} Reference metrics.csv'.format(sample, reference), index=False)

## Plot Heatmap with results

### Global

In [77]:
table_of_diff_global = glob.glob('Tables/*Global metrics.csv')
import plotly.figure_factory as ff
for table in table_of_diff_global:
    sample = table.split('/')[-1].split(' ')[0]
    data = pd.read_csv(table)
    x=['Contigs','Basepairs','Max Contig Size','N','N50','Misassemblies','Mapped Reads']
    y=list(data['Assembler'])
    z=data[['Contigs','Basepairs','Max Contig Size','N','N50','Misassemblies','Mapped Reads']].to_numpy()
    fig = ff.create_annotated_heatmap(z=z,x=x,y=y, colorscale='Greys', showscale=True)
    fig.update_layout(title={'text': sample,
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'})
    fig.show()
    plot(fig, auto_open=False, filename="Plots/Heatmaps/{} Global metrics".format(sample))
    

/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/LNN Global metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ERR2984773 Global metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/EHS Global metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/LHS Global metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ENN Global metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ERR2935805 Global metrics` didn't end with .html. Adding .html to the end of your file.



### Per Reference

In [ ]:
table_of_diff_ref = glob.glob('Tables/*Reference metrics.csv')
for table in table_of_diff_ref:
    sample = table.split('/')[-1].split(' ')[0]
    reference = table.split('/')[-1].split(' ')[1].replace('_',' ')
    data = pd.read_csv(table)
    x=['Contiguity','Breadth of Coverage', 'Multiplicity', 'Validity', 'Parsimony', 'Identity',
       'lowest Identity', 'L90', 'Contigs', 'NA50', 'NG50', 'Basepairs', 'Ns', 'Misassemblies']
    y=list(data['Assembler'])
    z=data[['Contiguity','Breadth of Coverage', 'Multiplicity', 'Validity', 'Parsimony', 'Identity',
       'lowest Identity', 'L90', 'Contigs', 'NA50', 'NG50', 'Basepairs', 'Ns', 'Misassemblies']].to_numpy()
    fig = ff.create_annotated_heatmap(z=z,x=x,y=y, colorscale='Greys', showscale=True)
    fig.update_layout(title={'text':'{} {}'.format(sample, reference),
        'y':0.9,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'})
    fig.show()
    plot(fig, auto_open=False, filename="Plots/Heatmaps/{} {} Reference metrics".format(sample, reference))
    

/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/LNN Lactobacillus fermentum Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ENN Staphylococcus aureus plasmid3 Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/LHS Staphylococcus aureus plasmid3 Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ERR2984773 Staphylococcus aureus plasmid3 Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ERR2984773 Enterococcus faecalis Reference metrics` didn't end with .html. Adding .html to the end of your file.



...

/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ENN Escherichia coli plasmid Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/LNN Staphylococcus aureus Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ENN Bacillus subtilis Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/EHS Pseudomonas aeruginosa Reference metrics` didn't end with .html. Adding .html to the end of your file.



/home/ines/.local/lib/python3.9/site-packages/plotly/offline/offline.py:562: UserWarning:

Your filename `Plots/Heatmaps/ERR2935805 Escherichia coli Reference metrics` didn't end with .html. Adding .html to the end of your file.

